# [버지니아 공대](http://www.cs.virginia.edu/~hw5x/Course/IR2015/_site/lectures/)

- 텍스트 데이터를 넣을 때 의미 표현 때문에 벡터로 만든다.
- 룰베이스, 워드넷 사전 정보, 온톨로지를 사용해서 할 수도 있고, 이게 대안이 되진 않는다. 
    - 사전은 끊임없이 업데이트 해야되고 온톨로지도 사람이 계속 의미를 만들어줘야함
- 워드임베딩에서는 weight값이 어떻게 조절 되었는지가 중요하다.
- 의미적으로 유사한 애들이 뭉쳐있는지 관계

## 정보검색
- information need : 검색 (query) ~이 필요해서 입력해서 검색
- collection = stored data  크롤러가 돌아다니면서 정보를 긁어오면 stored data
- 쿼리와 가장 relevant한 data를 돌려준다. 
- 벡터와 벡터의 관계

### metadata : 해시태그 
- 요즘은 메타데이터가 별로 필요가 없다.

### full-text indexing
- 전체 문서를 어떻게 색인 할 것인가

#### unstructured data를 어떻게 처리할것인가?
- where, on 절을 가지고 정보를 가지고 오지만 해당 키워드를 가지고 있는 것을 모두 가지고 온다.
- db를 가지고 하면 사용자가 찾고 싶은 것과 얼마나 가까운지 뭘 원했는지 정확하게 모른다.

#### text-mining에서 검색이 왜 중요한가?
- 추천을 할 수 있다.
- 단순한 웹 서치가 아니다.
- QnA도 검색을 기반으로 하고 있다. 챗봇 또한 그렇다.
- 토픽 찾는 프로그램 -> 비지도 학습 모델로 한다.

- 가져와서 분석해서 렉시콘에 넣어줘야하는데 실시간이 검색이 잘 안 되는 이유는 이 과정이 아직 진행되지 않아서


- 로그들을 가지고 동일한 키워드에 대해서 사람마다 다른 것을 보여준다. - 개인화, 맞춤형
- 사람들이 클릭하면 렉시콘의 가중치를 높이고 클릭하지 않은 것은 렉시콘을 낮추는 형태로 진행

#### core concept
- say, said -> 컴퓨터는 다른 심볼로 인식할 것이다.
- Document representation 에서 나오는 것이 맵리듀스 나옴. 하둡 에코시스템
- retrival model

http://bitly.kr/85NpbM

In [1]:
import sqlite3
con = sqlite3.connect("news.db")
cur = con.cursor()

cur.execute("""
    SELECT content
    FROM table2
    ORDER BY id ASC
""")
#corpus는 db에 저장 되어있는 기사들이 저장 되어 있는 리스트
# fetchall()하면 리스트 안에 튜플 형식으로 들어있으므로 하나씩 꺼내서 리스트에 담아준다.
news = cur.fetchall()
corpus = [_[0] for _ in news]

In [2]:
def eojeol(sentence, N=2):
    tokens = word_tokenize(sentence)
    ngram = list()
    for i in range(len(tokens)-(N-1)):
#         ngram.append(" ".join(tokens[i:i+N]))
        ngram.append(tuple(tokens[i:i+N]))
    return ngram


def umjeol(token, N=2):
    tokens = list(token)
    ngram = list()
    for i in range(len(tokens)-(N-1)):
        ngram.append("".join(tokens[i:i+N]))
#         ngram.append(tuple(tokens[i:i+N]))
    return ngram

In [8]:
!pip install --user JPype1-0.6.3-cp37-cp37m-win_amd64.whl

In [9]:
!pip install konlpy

In [3]:
from konlpy.tag import Kkma
# .pos()는 형태소와 품사 쌍으로 결과를 반환해준다.
Kkma().pos('아이스크림 값 10만원...')

[('아이스크림', 'NNG'),
 ('값', 'NNG'),
 ('10', 'NR'),
 ('만', 'NR'),
 ('원', 'NNM'),
 ('...', 'SE')]

Pre-processing (RE)

Tokenization -> Ngram -> Stemming/Normalization(길이, 빈도) -> Stopwords

In [4]:
import re
from string import punctuation
from nltk.tokenize import word_tokenize

# word_tokenize(corpus[0])
pattern1 = re.compile(r"[{0}]".format(re.escape(punctuation))) # 구두점들을 찾아주는 정규식
# pattern1.sub("",corpus[0]) # 구두점들을 날린다.
pattern2 = re.compile(r"[A-Za-z]{5,}") # 영어 5글자 이상인 것을 찾아주는 정규식
# pattern2.sub("", pattern1.sub("",corpus[0])) # 구두점이랑 영어를 싹 날린다.
pattern3 = re.compile(r"[^ \n0-9A-Za-z가-힣]") # 특수 문자를 날릴 거다.
# pattern3.sub("",pattern2.sub("", pattern1.sub("",corpus[0])))
pattern4 = re.compile(r"\s{2,}")

#정규식으로 필요 없는 문자를 싹 삭제 했다. -> Tokenizing 할 준비가 됨
collection = list()
for _ in corpus:
    collection.append(pattern4.sub(" ",
            pattern3.sub(" ",
            pattern2.sub(" ", 
            pattern1.sub("",_)))).strip())

In [18]:
collection

['합리적 보수 주춧돌 되길 바랐는데 줄지어 추모 정두언 빈소 찾은 조문객들서울연합뉴스 신준희 기자 17일 서울 서대문구 세브란스병원 장례식장에 마련된 고 정두언 전 새누리당 의원의 빈소에서 조문객들이 조문하고 있다 서울연합뉴스 방현덕 기자 고 정두언 의원의 사망 이튿날인 17일 차려진 빈소에는 여야 정치권 인사들의 조문 행렬이 이어졌다 자유한국당 김성태 전 원내대표는 오후 서울 신촌 세브란스 병원 빈소를 찾은 뒤 기자들과 만나 대한민국 보수 정치의 큰 족적을 남기신 훌륭한 정치인인데 이렇게 허무하게 간다는 게 믿어지지 않는다며 남아있는 우리가 제대로 된 보수 정당의 면모를 굳히겠다고 밝혔다 동행한 한국당 장제원 의원은 TV를 켜면 바로 볼 수 있는 선배였는데 이제는 볼 수 없다고 생각하니 가슴이 미어진다며 내년 총선에 우리 원내에 들어와 합리적 보수를 세울 수 있는 주춧돌 역할을 해주길 바랐는데 속절없이 떠나 정신이 멍하다고 했다 빈소 조문하는 김성태장제원서울연합뉴스 신준희 기자 자유한국당 김성태오른쪽 장제원 의원이 17일 오후 서울 신촌 세브란스병원 장례식장에 마련된 고 정두언 전 새누리당 의원 빈소를 조문하고 있다 바른미래당 유승민 의원은 같은 당 정병국 이혜훈 유의동 의원과 함께 조문한 뒤 마지막까지 고인이 혼자 감당했을 괴로움을 제가 다 헤아릴 수 없다 가슴이 아프다라고 했다 지난 17대 국회부터 나란히 의정활동을 시작한 유 의원과 정 전 의원은 친구이자 동료였지만 2007년에는 각각 박근혜 이명박 당시 대선후보 캠프의 책사로서 치열한 경선전을 펼치기도 했다 고 정두언 의원 빈소 찾은 유승민서울연합뉴스 신준희 기자 바른미래당 유승민 지상욱 정병국 이혜훈 의원 등이 17일 오전 서울 신촌 세브란스병원 장례식장에 마련된 고 정두언 전 새누리당 의원 빈소를 조문하고 있다 같은 당 하태경 의원도 조문 후 정 전 의원의 죽음은 대한민국 개혁보수 진영 입장에서도 큰 걱정이라며 그가 이뤄내려 했던 부분을 남아있는 후배들이 반드시 이루어낼 것이라고 말했다 정몽준 아

In [5]:
kkma = Kkma()
kkma.pos("아직 목요일이라니.."), kkma.morphs("아직 목요일이라니..") # 품사, 형태소 
# N -> 명사 V -> 동사

([('아직', 'MAG'),
  ('목요일', 'NNG'),
  ('이', 'VCP'),
  ('라', 'ECD'),
  ('니', 'NP'),
  ('..', 'SW')],
 ['아직', '목요일', '이', '라', '니', '..'])

In [6]:
# Tokenization
# 어절(띄어쓰기 단위로 구분) 있는 그대로 사용
# 조금 더 자연스러운 처리를 하려면 형태소를 사용해야 한다.
# Ngram도 사용해야 한다 왜???는 놓침 ㅠㅠ

# 구두점이 날라갔으니까 word_tokenizer가 소용이 없다.
# from nltk.tokenize import word_tokenize
# len(word_tokenize(collection[0])), len(collection[0].split())

# corpus[0].split() => BoM
# 바이그램을 사용해서 띄어쓰기를 고려했더니 뻥튀기 됨.(umjeol)
len(collection[0].split()), len(eojeol(collection[0])), \
len(umjeol(collection[0])), len(kkma.morphs(collection[0])) # kkma -> feature의 수 

(431, 430, 1727, 950)

In [7]:
Vocabulary = list()
for _ in collection:
    Vocabulary.extend(_.split())
    Vocabulary.extend(eojeol(_))
    Vocabulary.extend(umjeol(_))
    Vocabulary.extend(kkma.morphs(_))

In [8]:
len(Vocabulary), len(set(Vocabulary))

(111299, 28856)

Tokenization

--------------------------------

Normalization, Stopwords(비속어, 품사)

In [9]:
Vocabulary = [_ for _ in list(set(Vocabulary)) if 1 < len(_) < 6] # 한 단어인거, 너무 큰거 걸러낼 수 있다.
len(Vocabulary)

27852

얘를 이용해서 어미 등 필요 없는거 잘라낼 수 있다.

In [34]:
kkma.tagset

{'EC': '연결 어미',
 'ECD': '의존적 연결 어미',
 'ECE': '대등 연결 어미',
 'ECS': '보조적 연결 어미',
 'EF': '종결 어미',
 'EFA': '청유형 종결 어미',
 'EFI': '감탄형 종결 어미',
 'EFN': '평서형 종결 어미',
 'EFO': '명령형 종결 어미',
 'EFQ': '의문형 종결 어미',
 'EFR': '존칭형 종결 어미',
 'EP': '선어말 어미',
 'EPH': '존칭 선어말 어미',
 'EPP': '공손 선어말 어미',
 'EPT': '시제 선어말 어미',
 'ET': '전성 어미',
 'ETD': '관형형 전성 어미',
 'ETN': '명사형 전성 어미',
 'IC': '감탄사',
 'JC': '접속 조사',
 'JK': '조사',
 'JKC': '보격 조사',
 'JKG': '관형격 조사',
 'JKI': '호격 조사',
 'JKM': '부사격 조사',
 'JKO': '목적격 조사',
 'JKQ': '인용격 조사',
 'JKS': '주격 조사',
 'JX': '보조사',
 'MA': '부사',
 'MAC': '접속 부사',
 'MAG': '일반 부사',
 'MD': '관형사',
 'MDN': '수 관형사',
 'MDT': '일반 관형사',
 'NN': '명사',
 'NNB': '일반 의존 명사',
 'NNG': '보통명사',
 'NNM': '단위 의존 명사',
 'NNP': '고유명사',
 'NP': '대명사',
 'NR': '수사',
 'OH': '한자',
 'OL': '외국어',
 'ON': '숫자',
 'SE': '줄임표',
 'SF': '마침표, 물음표, 느낌표',
 'SO': '붙임표(물결,숨김,빠짐)',
 'SP': '쉼표,가운뎃점,콜론,빗금',
 'SS': '따옴표,괄호표,줄표',
 'SW': '기타기호 (논리수학기호,화폐기호)',
 'UN': '명사추정범주',
 'VA': '형용사',
 'VC': '지정사',
 'VCN': "부정 지정사, 형용사 '아니다'",
 'VC

무식하게 만든 것이다. 이렇게 만들면 느리고 처리할게 너무 많다. for문에 if문이 많다-> 잘못만든거

In [10]:
# BoM = list(0 for _ in range(len(Vocabulary)))
BoM = list() # docVector 모음
for d in collection: # documents 하나씩 반복 처리
    docVector = list(0 for _ in range(len(Vocabulary))) # 문서의 벡터 
    for _ in d.split() + eojeol(d)+ umjeol(d) + kkma.morphs(d): # 문서를 쪼갠 것들을 하나씩 꺼낸다.
        if _ in Vocabulary: # 문서를 조각낸 것이 Vocabulary에 있으면
            docVector[Vocabulary.index(_)] = 1 # docVector에 Vocabulary에서 _가 있는 위치에 docVector 1로 표시
    BoM.append(docVector) # 완성된 docVector를 append 해준다

In [14]:
BoM

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,


In [20]:
import numpy as np
len(Vocabulary) - sum(BoM[0])

26540

In [14]:
BoM

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [21]:
# 문제점1 : Sparse하다 (복잡도가 증가한다)
[(sum(_), len(Vocabulary)) for _ in BoM]

[(1312, 27852),
 (1838, 27852),
 (1123, 27852),
 (1420, 27852),
 (1109, 27852),
 (1622, 27852),
 (1776, 27852),
 (1810, 27852),
 (1364, 27852),
 (1620, 27852),
 (1616, 27852),
 (883, 27852),
 (1444, 27852),
 (1874, 27852),
 (1337, 27852),
 (1880, 27852),
 (1257, 27852),
 (1048, 27852),
 (482, 27852),
 (734, 27852),
 (1956, 27852),
 (1983, 27852),
 (870, 27852),
 (815, 27852),
 (1236, 27852),
 (1748, 27852),
 (1747, 27852),
 (1553, 27852),
 (1187, 27852),
 (1401, 27852),
 (1269, 27852),
 (825, 27852),
 (665, 27852),
 (1342, 27852),
 (1549, 27852)]

In [19]:
Query = ["국민", "법안"]
totalResult = list()
for q in Query:
    searchResult = list()
    for i, d in enumerate(BoM):
        for j, b in enumerate(d):
            if b == 1 and j == Vocabulary.index(q):
                searchResult.append(i)
                break
    totalResult.append(searchResult)
# Vocabulary.index("국민"), Vocabulary.index("법안")

In [23]:
set(totalResult[0]).intersection(totalResult[1])

{6, 8, 34}

## inverted index
- term을 가지고 document를 표현했다.

In [13]:
from collections import defaultdict

#doc -> term:freq : 문장에 어떤 단어들이 얼마나 나왔는지
DTM = defaultdict(lambda:defaultdict(int))
for i, d in enumerate(BoM):
    for j, t in enumerate(d):
        if t == 1:
            DTM[i][j] = t
            
# Sparse : 90% 0인 부분을 줄일 수 있다.

In [14]:
DTM[0]

defaultdict(int,
            {19: 1,
             20: 1,
             53: 1,
             90: 1,
             144: 1,
             201: 1,
             204: 1,
             232: 1,
             237: 1,
             254: 1,
             273: 1,
             297: 1,
             321: 1,
             351: 1,
             454: 1,
             482: 1,
             483: 1,
             492: 1,
             516: 1,
             543: 1,
             554: 1,
             567: 1,
             579: 1,
             586: 1,
             641: 1,
             647: 1,
             655: 1,
             661: 1,
             666: 1,
             677: 1,
             697: 1,
             739: 1,
             763: 1,
             793: 1,
             795: 1,
             808: 1,
             812: 1,
             828: 1,
             846: 1,
             894: 1,
             897: 1,
             919: 1,
             988: 1,
             1042: 1,
             1086: 1,
             1099: 1,
             1107:

In [15]:
sum(DTM[0].values())

1312

In [16]:
TDM = defaultdict(lambda:defaultdict(int))
for i, termDict in DTM.items():
    for j, b in termDict.items():
        TDM[j][i] = b
        
# 정보 검색을 할 떄 complexity를 줄일 수 있다.

BoM = O(|Q| * D * |D|)


TDM = O(|Q| * avg(|D|))

In [21]:
searchResult = list()
for q in Query:
    j = Vocabulary.index(q)
#     TDB[j].keys() # 문서 번호
    searchResult.append(list(TDM[j].keys()))

In [23]:
set(searchResult[0]).intersection(searchResult[1])

{6, 8, 34}

벡터라이즈 한다고 하면 BoM, TDM 이 기본 구조이다.

다시 벡터화 할 수 있다.

In [24]:
termVector = list(list(0 for _ in range(len(collection)))
                 for _  in range(len(Vocabulary)))
for j, docDict in TDM.items():
    for i in range(len(collection)):
        termVector[j][i] = docDict[i]

In [25]:
termVector

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [26]:
import numpy as np
_BoM = np.array(termVector)

BoM[0] == \_BoM.T[0]

In [28]:
_BoM.T[0]

array([0, 0, 0, ..., 0, 0, 1])

In [30]:
sum(BoM[0]), sum(_BoM.T[0])

(1312, 1312)

복잡도가 낮아지고, 공간이 줄었고, 빨라졌다.

다음과 같이 두가지로 쪼갤거다. (Dictionary, Posting)

In [32]:
D = [
    ["A", "B"],
    ["C", "D"],
    ["A", "C"],
]

# TDM, "A" : {0:freq, 1:freq}
# TDM = Dictionary
# "A":0
# Posting
# [
#     0: 어느문서, freq, 1
#     1: djsmanstj, freq, -1
# ]


Dictionary = defaultdict(lambda:-1) # -1이면 더이상 없는 형태 0부터 시작할거기 때문에?
Postings = list()

# 전체 단어 목록 추출
V = list()

for j, d in enumerate(D): # document를 뒤져서 
    for t in d: # term이 나올거고
        if t not in V: # V에 없으면 추가해준다.
            V.append(t)
        i = V.index(t) # t의 V에서 index
        nextPosition = Dictionary[i] # 다음 것이 없으면 -1이다.
        _struct = (j, 1, nextPosition) # 몇 번 째 문서에서, 몇 번 나왔고, 다음 위치는 어디인가
        Dictionary[i] = len(Postings)
        Postings.append(_struct) # 몇 번째 문서에서 몇 번 나왔는지 정보를 저장해줄거임
        

In [33]:
Postings

[(0, 1, -1), (0, 1, -1), (1, 1, -1), (1, 1, -1), (2, 1, 0), (2, 1, 2)]

In [40]:
Q = ["A"]

for q in Q:
    i = V.index(q)
    nextPosition = Dictionary[i]
    while True:
        _struct = Postings[nextPosition]
        nextPosition = _struct[2]
        print("{0}번째 문서, {1}번, 다음위치:{2}".format(_struct[0]+1, _struct[1], _struct[2]))
        if nextPosition == -1:
            break
        nextPosition = _struct[2]

3번째 문서, 1번, 다음위치:0
1번째 문서, 1번, 다음위치:-1


In [41]:
D[0], D[2]

(['A', 'B'], ['A', 'C'])

In [60]:
D = [
    ["A", "B"],
    ["C", "D"],
    ["A", "C"],
]


Dictionary = defaultdict(lambda:-1) # -1이면 더이상 없는 형태 0부터 시작할거기 때문에?
Postings = open('postings.dat', 'w')

# 전체 단어 목록 추출
V = list()

for j, d in enumerate(D): # document를 뒤져서 
    for t in d: # term이 나올거고
        if t not in V: # V에 없으면 추가해준다.
            V.append(t)
        i = V.index(t) # t의 V에서 index
        nextPosition = Dictionary[i] # 다음 것이 없으면 -1이다.
        _struct = (str(j), str(1), str(nextPosition)) # 몇 번 째 문서에서, 몇 번 나왔고, 다음 위치는 어디인가
        print(_struct)
        Dictionary[i] = Postings.tell() # 위치를 반환 
        print(",".join(_struct))
        Postings.write(",".join(_struct)+"\n") # 몇 번째 문서에서 몇 번 나왔는지 정보를 저장해줄거임

Postings.close()        

('0', '1', '-1')
0,1,-1
('0', '1', '-1')
0,1,-1
('1', '1', '-1')
1,1,-1
('1', '1', '-1')
1,1,-1
('2', '1', '0')
2,1,0
('2', '1', '16')
2,1,16


In [61]:
Q = ["C"]
Postings = open('postings.dat', 'r')

for q in Q:
    i = V.index(q)
    nextPosition = Dictionary[i]
    while True:
        Postings.seek(nextPosition)
        _struct = [int(_.strip())
                   for _ in Postings.readline().split(",")]
        nextPosition = int(_struct[2])
        print("{0}번째 문서, {1}번, 다음위치:{2}".format(_struct[0], _struct[1], _struct[2]))
        # 위치가 str이므로 1byte씩 먹었을 거잖아요 그래서 16이 나와요
        if nextPosition == -1:
            break
        nextPosition = _struct[2]
Postings.close()

2번째 문서, 1번, 다음위치:16
1번째 문서, 1번, 다음위치:-1


In [62]:
from struct import pack, unpack # byte array로 바꾸는 과정

D = [
    ["A", "B"],
    ["C", "D"],
    ["A", "C"],
]


Dictionary = defaultdict(lambda:-1)
Postings = open('postings.dat', 'wb') # 바이트로 저장할거에요


V = list()

for j, d in enumerate(D): 
    for t in d: 
        if t not in V: 
            V.append(t)
        i = V.index(t) 
        nextPosition = Dictionary[i] 
        _struct = pack("iii", j, 1, nextPosition) # format -> integer 4byte로 3개 넣겠다.
        Dictionary[i] = Postings.tell()
        Postings.write(_struct) 

Postings.close()        

In [55]:
with open('postings.dat', 'rb') as fp:
    print(fp.read())

b'\x00\x00\x00\x00\x01\x00\x00\x00\xff\xff\xff\xff\x00\x00\x00\x00\x01\x00\x00\x00\xff\xff\xff\xff\x01\x00\x00\x00\x01\x00\x00\x00\xff\xff\xff\xff\x01\x00\x00\x00\x01\x00\x00\x00\xff\xff\xff\xff\x02\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x02\x00\x00\x00\x01\x00\x00\x00\x18\x00\x00\x00'


In [63]:
Q = ["C"]
Postings = open('postings.dat', 'rb') # byte로 저장했으니 바이트로 불러와서 

for q in Q:
    i = V.index(q)
    nextPosition = Dictionary[i]
    while True:
        Postings.seek(nextPosition)
        _struct = unpack("iii", Postings.read(4*3)) # 4 byte로 3개 불러오겠다.
#         print(_struct)
        nextPosition = _struct[2]
        print("{0}번째 문서, {1}번, 다음위치:{2}".format(_struct[0], _struct[1], _struct[2]))
        if nextPosition == -1:
            break
        nextPosition = _struct[2]

Postings.close()

2번째 문서, 1번, 다음위치:24
1번째 문서, 1번, 다음위치:-1


In [65]:
from struct import pack, unpack # byte array로 바꾸는 과정

D = [
    ["A", "B"],
    ["C", "D"],
    ["A", "C"],
]

V = list()

for j, d in enumerate(D): 
    for t in d: 
        if t not in V: 
            V.append(t)
        i = V.index(t) 
        TDM[i][j] = 1
      

In [66]:
TDM

defaultdict(<function __main__.<lambda>()>,
            {19: defaultdict(int,
                         {0: 1,
                          1: 0,
                          2: 0,
                          3: 0,
                          4: 0,
                          5: 0,
                          6: 0,
                          7: 0,
                          8: 0,
                          9: 0,
                          10: 0,
                          11: 0,
                          12: 0,
                          13: 0,
                          14: 0,
                          15: 0,
                          16: 0,
                          17: 0,
                          18: 0,
                          19: 0,
                          20: 0,
                          21: 0,
                          22: 0,
                          23: 0,
                          24: 0,
                          25: 0,
                          26: 0,
                          27: 0,
        

In [72]:
%%timeit
Q = ["A", "C"]

for q in Q:
    i = V.index(q)
    
    for d, b in TDM[i].items():
        print("{0}번째 문서, {1}번".format(d,b))

6.82 µs ± 562 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)


# 빈도 까지 적용

In [73]:
V = list()
D = list()

DTM = defaultdict(lambda:defaultdict(int))


for d in collection:
    i = len(D)
    D.append(i)
    
#     ("형태소", "품사") 형태로 나옴
    for t in [_[0] for _ in kkma.pos(d) if _[1].startswith("N")]:
        if t not in V:
            V.append(t)
        j = V.index(t)
        DTM[i][j] += 1

계산 량이 줄었다.

In [74]:
len(V), len(D)

(3306, 35)

In [75]:
TDM = defaultdict(lambda:defaultdict(int))

for i, terms in DTM.items():
    for j, f in terms.items():
        TDM[j][i] = f

file에 있을 때 와 리스트에 있는거를 확인해야 됨

In [83]:
%%timeit
for t, docs in TDM.items():
    for d, f in docs.items():
        print(V[j], D[i], f)
    print()
    
# 2.9 s ± 270 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)

흥 1 2
흥 1 1

흥 1 5
흥 1 1
흥 1 1

흥 1 2

흥 1 2

흥 1 18
흥 1 8
흥 1 3
흥 1 2
흥 1 3
흥 1 1
흥 1 4
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 13

흥 1 2

흥 1 14
흥 1 3
흥 1 2
흥 1 6
흥 1 4
흥 1 5
흥 1 2
흥 1 6
흥 1 8
흥 1 6
흥 1 6
흥 1 6
흥 1 1
흥 1 3
흥 1 1
흥 1 3
흥 1 1
흥 1 1

흥 1 9
흥 1 6
흥 1 5
흥 1 4
흥 1 7
흥 1 1
흥 1 1
흥 1 5
흥 1 3
흥 1 1
흥 1 1
흥 1 4
흥 1 6
흥 1 1

흥 1 9
흥 1 5
흥 1 5
흥 1 2
흥 1 4
흥 1 7
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 3
흥 1 5
흥 1 2
흥 1 2
흥 1 2
흥 1 4
흥 1 2
흥 1 2
흥 1 1
흥 1 1

흥 1 6
흥 1 1
흥 1 1

흥 1 8
흥 1 4
흥 1 3
흥 1 4
흥 1 2
흥 1 5
흥 1 2
흥 1 4
흥 1 4
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 2
흥 1 2
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 4

흥 1 8
흥 1 2
흥 1 4
흥 1 1
흥 1 2
흥 1 4
흥 1 1
흥 1 3
흥 1 2
흥 1 1
흥 1 1
흥 1 2
흥 1 2
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 4
흥 1 4
흥 1 2
흥 1 1
흥 1 1
흥 1 1

흥 1 7
흥 1 6
흥 1 5
흥 1 8
흥 1 2
흥 1 6
흥 1 11
흥 1 5
흥 1 7
흥 1 5
흥 1 4
흥 1 1
흥 1 4
흥 1 3
흥 1 1
흥 1 6
흥 1 3
흥 1 3
흥 1 2
흥 1 2
흥 1 1
흥 1 1

흥 1 2
흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 5
흥 1 1
흥 1 1
흥 1 2
흥 1 3
흥 1 2
흥 1 1
흥 1 2
흥 1 1
흥 1 2
흥 1 3
흥 1 1
흥 1 1
흥 1 5
흥 1 3
흥 1 2
흥 1 2
흥 1 2
흥 1 1
흥 1 2
흥 1 3

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 2
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 1

흥 1 2
흥 1 1

흥 1 3

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 3
흥 1 2
흥 1 6
흥 1 5
흥 1 4
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 1

흥 1 2

흥 1 1
흥 1 3

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 1

흥 1 3
흥 1 2
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 6
흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 3
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 2
흥 1 1
흥 1 1
흥 1 4

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 2

흥 1 1

흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 1
흥 1 3
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 4
흥 1 1

흥 1 3
흥 1 8

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1


흥 1 1

흥 1 1

흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 15
흥 1 1

흥 1 2

흥 1 5

흥 1 2

흥 1 2

흥 1 5
흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 14
흥 1 11
흥 1 1
흥 1 6

흥 1 2
흥 1 1
흥 1 1

흥 1 1
흥 1 3
흥 1 2

흥 1 11
흥 1 5

흥 1 8
흥 1 2

흥 1 3
흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 2

흥 1 1
흥 1 2
흥 1 2
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 1

흥 1 3
흥 1 4
흥 1 1
흥 1 7

흥 1 2
흥 1 1

흥 1 2

흥 1 3

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 5

흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 3
흥 1 3

흥 1 1
흥 1 1
흥 1 3
흥 1 1

흥 1 6
흥 1 3
흥 1 2
흥 1 1
흥 1 6
흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 2

흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 2
흥 1 1

흥 1 1
흥 1 5
흥 1 1
흥 1 1
흥 1 3

흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 3
흥 1 1

흥 1 5
흥 1 6

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 3
흥 1 11
흥 1 1

흥 1 3

흥 1 1

흥 1 3
흥 1 3
흥 1 1

흥 1 2
흥 1 1
흥 1 1
흥 1 1
흥 1 5

흥 1 2

흥 1 1

흥 1 2
흥 1 1

흥 1 1
흥 1 1
흥 1 3
흥 1 1
흥 1 1

흥 1 2
흥 1 1
흥 1 1
흥 1

흥 1 1

흥 1 1

흥 1 2

흥 1 2
흥 1 1
흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 2
흥 1 2

흥 1 1
흥 1 2

흥 1 1
흥 1 2

흥 1 3
흥 1 3
흥 1 6

흥 1 1

흥 1 2

흥 1 1

흥 1 1
흥 1 1

흥 1 2

흥 1 2
흥 1 1
흥 1 1

흥 1 1

흥 1 4

흥 1 4

흥 1 4

흥 1 2

흥 1 2

흥 1 4
흥 1 4

흥 1 3

흥 1 4

흥 1 6

흥 1 5
흥 1 2

흥 1 2

흥 1 3
흥 1 2

흥 1 1

흥 1 3

흥 1 3

흥 1 13
흥 1 10

흥 1 3

흥 1 1

흥 1 3
흥 1 3

흥 1 2

흥 1 2
흥 1 1

흥 1 3

흥 1 3
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3
흥 1 2
흥 1 1

흥 1 1
흥 1 1

흥 1 2

흥 1 4
흥 1 2
흥 1 2

흥 1 4

흥 1 3

흥 1 2

흥 1 1

흥 1 1
흥 1 2

흥 1 1
흥 1 1
흥 1 1

흥 1 3

흥 1 7
흥 1 1

흥 1 4

흥 1 1

흥 1 4

흥 1 2

흥 1 1

흥 1 1
흥 1 2

흥 1 1

흥 1 2

흥 1 11
흥 1 2

흥 1 2

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 6
흥 1 2

흥 1 5

흥 1 1

흥 1 1

흥 1 2
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 3

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 5

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 3

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 9

흥 1 1

흥 1 1

흥 1 1



흥 1 1

흥 1 7

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 5

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 2

흥 1 1

흥 1 7

흥 1 3

흥 1 3

흥 1 2

흥 1 2

흥 1 15

흥 1 3

흥 1 2

흥 1 1

흥 1 1

흥 1 4

흥 1 2

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 5

흥 1 1

흥 1 8

흥 1 2

흥 1 3

흥 1 1

흥 1 1

흥 1 3

흥 1 2

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 5

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 2
흥 1 10
흥 1 9

흥 1 3

...

흥 1 1
흥 1 1

흥 1 2
흥 1 1

흥 1 2

흥 1 2
흥 1 1

흥 1 2
흥 1 1

흥 1 1
흥 1 2

흥 1 2
흥 1 8
흥 1 1
흥 1 1
흥 1 5
흥 1 3
흥 1 4
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 2
흥 1 2
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 3
흥 1 1
흥 1 9
흥 1 7
흥 1 3

흥 1 3
흥 1 2

흥 1 3

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 4
흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 2
흥 1 1
흥 1 4
흥 1 3
흥 1 1
흥 1 3
흥 1 1
흥 1 1
흥 1 9

흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 1
흥 1 3

흥 1 1

흥 1 1
흥 1 1
흥 1 2

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 3
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 2
흥 1 5
흥 1 24
흥 1 3
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 5

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 3

흥 1 1
흥 1 2

흥 1 1
흥 1 2

흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 4
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 3
흥 1 1
흥 1 2
흥 1 1
흥 1 3
흥 1 6
흥 1 6
흥 1 1
흥 1 3
흥 1 2
흥 1 2
흥 1 2
흥 1 5
흥 1 4
흥 1 3
흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 4

흥 1 1
흥 1 1
흥 1 2

흥 1 2
흥 1 1
흥 1 1
흥 1 5
흥 1 1
흥 1 2
흥 1 1
흥 1 3
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 2

흥 1 1
흥 1 1
흥 1 1
흥 1 2

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 2
흥 1 1

흥 1 2

흥 1 2

흥 1 1
흥 1 1

흥 1 5
흥 1 8
흥 1 1
흥 1 1

흥 1 6
흥 1 4
흥 1 5
흥 1 6

흥 1 4
흥 1 3
흥 1 5

흥 1 2

흥 1 7
흥 1 5

흥 1 2
흥 1 2

흥 1 1
흥 1 1
흥 1 1

흥 1 2
흥 1 6
흥 1 1
흥 1 6

흥 1 2
흥 1 6
흥 1 1
흥 1 6

흥 1 1

흥 1 1

흥 1 3
흥 1 1

흥 1 6
흥 1 1
흥 1 2

흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 9
흥 1 12
흥 1 1
흥 1 1
흥 1 2
흥 1 4
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 9
흥 1 2
흥 1 1
흥 1 21
흥 1 1
흥 1 16
흥 1 14
흥 1 25
흥 1 8
흥 1 16
흥 1 2

흥 1 3
흥 1 1
흥 1 7
흥 1 2
흥 1 2
흥 1 3
흥 1 8
흥 1 3
흥 1 2

흥 1 3
흥 1 3
흥 1 1
흥 1 3
흥 1 6
흥 1 2
흥 1 3
흥 1 3
흥 1 4
흥 1 3
흥 1 2
흥 1 4
흥 1 4

흥 1 1
흥 1 1
흥 1 1
흥 1 3
흥 1 1
흥 1 5
흥 1 4

흥 1 2
흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 3
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 5
흥 1 2
흥 1 3
흥 1 8

흥 1 2
흥 1 1
흥 1 1
흥 1 1


흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 2
흥 1 4
흥 1 1
흥 1 2

흥 1 2

흥 1 2
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 4
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 3

흥 1 1
흥 1 2

흥 1 1

흥 1 1

흥 1 1
흥 1 2

흥 1 3
흥 1 1
흥 1 4

흥 1 2
흥 1 1
흥 1 2
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1

흥 1 2
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 24
흥 1 1

흥 1 3
흥 1 10
흥 1 3
흥 1 6

흥 1 2
흥 1 12

흥 1 1
흥 1 2
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 2
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1
흥 1 1
흥 1 2

흥 1 2
흥 1 6
흥 1 1

흥 1 1
흥 1 4

흥 1 3
흥 1 1
흥 1 1
흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 3
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 3
흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 5
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 2

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 2
흥 1 13
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 4

흥 1 1
흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 2
흥 1 1

흥 1 1

흥 1 1
흥 1 2
흥 1 2
흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 2
흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 2
흥 1 5
흥 1 2
흥 1 1

흥 1 1
흥 1 4
흥 1 2

흥 1 3

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 2

흥 1 2
흥 1 1
흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1
흥 1 1
흥 1 1
흥 1 1

흥 1 1
흥 1 1

흥 1 2
흥 1 2

흥 1 1
흥 1 2

흥 1 1
흥 1 2

흥 1 3
흥 1 3
흥 1 6

흥 1 1

흥 1 2

흥 1 1

흥 1 1
흥 1 1

흥 1 2

흥 1 2
흥 1 1
흥 1 1

흥 1 1

흥 1 4

흥 1 4

흥 1 4

흥 1 2

흥 1 2

흥 1 4
흥 1 4

흥 1 3

흥 1 4

흥 1 6

흥 1 5
흥 1 2

흥 1 2

흥 1 3
흥 1 2

흥 1 1

흥 1 3

흥 1 3

흥 1 13
흥 1 10

흥 1 3

흥 1 1

흥 1 3
흥 1 3

흥 1 2

흥 1 2
흥 1 1

흥 1 3

흥 1 3
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3
흥 1 2
흥 1 1

흥 1 1
흥 1 1

흥 1 2

흥 1 4
흥 1 2
흥 1 2

흥 1 4

흥 1 3

흥 1 2

흥 1 1

흥 1 1
흥 1 2

흥 1 1
흥 1 1
흥 1 1

흥 1 3

흥 1 7
흥 1 1

흥 1 4

흥 1 1

흥 1 4

흥 

흥 1 2

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 5

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 2
흥 1 10
흥 1 9

흥 1 3

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 3

흥 1 1
흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 1

흥 1 1
흥 1 6

흥 1 1
흥 1 1

흥 1 1

흥 1 1
흥 1 3

흥 1 1

흥 1 2

흥 1 4
흥 1 4

흥 1 5
흥 1 4

흥 1 1

흥 1 1

흥 1 1

흥 1 11

흥 1 12

흥 1 1

흥 1 3

흥 1 3

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 1

흥 1 1
흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 1

흥 1 3

흥 1 1

흥 1 1

흥 1 2

흥 1 2

흥 1 1

흥 1 2

흥 1 1

흥 1 1

흥 1 1

흥 1 2

흥 1 6

In [97]:
V = list()
D = list()
Dictionary = defaultdict(lambda:-1)
Postings = list()

for d in collection:
    i = len(D)
    D.append(i)
    localPostings = defaultdict(int)
    
    for t in [_[0] for _ in kkma.pos(d) if _[1].startswith("N")]:
        if t not in V:
            V.append(t)
        j = V.index(t)
        localPostings[j] += 1
        
    for j, f in localPostings.items():
        nextPosition = Dictionary[j]
        _struct = (i, f, nextPosition)
        Dictionary[j] = len(Postings)
        Postings.append(_struct)

In [100]:
# 근소하게 빠르다.
%%timeit
for j in range(len(V)):
    nextPosition = Dictionary[j]
    while True:
        _struct = Postings[nextPosition]
        nextPosition = _struct[2]
        print(V[j], D[_struct[0]], _struct[1])
        if nextPosition == -1:
            break

UsageError: Line magic function `%%timeit` not found.


### file로 바꿉시다.

In [92]:
V = list()
D = list()
Dictionary = defaultdict(lambda:-1)
Postings = open('Postings.dat', 'w')

for d in collection:
    i = len(D)
    D.append(i)
    localPostings = defaultdict(int) # 빈도 저장해야되니 냅두자
    
    for t in [_[0] for _ in kkma.pos(d) if _[1].startswith("N")]:
        if t not in V:
            V.append(t)
        j = V.index(t)
        localPostings[j] += 1
        
    for j, f in localPostings.items():
        nextPosition = Dictionary[j]
        _struct = (i, f, nextPosition)
        Dictionary[j] = Postings.tell()
        Postings.write("{0},{1},{2}\n".format(
            _struct[0], _struct[1], _struct[2]))
        
Postings.close()

In [94]:
with open("Postings.dat", 'r') as Postings:
    for j in range(len(V)):
        nextPosition = Dictionary[j]
        while True:
            Postings.seek(nextPosition)
            _struct = [int(_.strip()) 
                       for _ in Postings.readline().split(",")]
            nextPosition = _struct[2]
            print(V[j], D[_struct[0]], _struct[1])
            if nextPosition == -1:
                break
                
# 4.57 s ± 255 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)

합리적 31 1
합리적 0 2
보수 7 1
보수 1 1
보수 0 5
주춧돌 0 2
추모 0 2
정 33 1
정 31 1
정 26 1
정 22 1
정 17 1
정 12 1
정 9 4
정 8 1
정 6 3
정 5 2
정 3 3
정 1 8
정 0 18
빈소 0 13
조문객 0 2
서울 34 1
서울 32 1
서울 30 3
서울 20 1
서울 19 3
서울 18 1
서울 16 6
서울 15 6
서울 14 6
서울 11 8
서울 10 6
서울 9 2
서울 8 5
서울 6 4
서울 4 6
서울 3 2
서울 1 3
서울 0 14
연합 30 1
연합 29 6
연합 28 4
연합 27 1
연합 26 1
연합 25 3
연합 23 5
연합 18 1
연합 15 1
연합 6 7
연합 4 4
연합 2 5
연합 1 6
연합 0 9
뉴스 33 1
뉴스 32 1
뉴스 30 2
뉴스 29 2
뉴스 28 4
뉴스 27 2
뉴스 26 2
뉴스 25 2
뉴스 23 5
뉴스 22 3
뉴스 21 2
뉴스 20 1
뉴스 18 1
뉴스 17 1
뉴스 16 1
뉴스 15 2
뉴스 14 1
뉴스 13 1
뉴스 11 1
뉴스 10 1
뉴스 7 2
뉴스 6 7
뉴스 4 4
뉴스 3 2
뉴스 2 5
뉴스 1 5
뉴스 0 9
신 15 1
신 1 1
신 0 6
기자 34 4
기자 33 1
기자 32 1
기자 31 2
기자 30 1
기자 29 1
기자 26 1
기자 25 1
기자 24 2
기자 23 2
기자 22 2
기자 21 2
기자 20 1
기자 19 1
기자 18 1
기자 17 1
기자 16 1
기자 15 1
기자 14 1
기자 13 1
기자 12 1
기자 11 1
기자 10 2
기자 9 4
기자 8 4
기자 7 2
기자 6 5
기자 4 2
기자 3 4
기자 2 3
기자 1 4
기자 0 8
17 32 1
17 30 1
17 28 1
17 27 2
17 26 4
17 23 4
17 20 1
17 19 1
17 18 2
17 17 1
17 16 1
17 15 1
17 14 2
17 13 2
17 12 2
17 11 

총회 7 2
총회 1 2
3 33 6
3 31 1
3 30 2
3 28 4
3 27 8
3 26 2
3 24 3
3 23 1
3 20 1
3 18 1
3 15 6
3 14 1
3 13 1
3 12 1
3 10 5
3 9 7
3 8 2
3 7 2
3 6 1
3 5 1
3 3 1
3 1 8
지대 20 1
지대 9 5
지대 1 6
주장 29 2
주장 27 1
주장 26 1
주장 22 1
주장 20 6
주장 17 2
주장 11 1
주장 9 3
주장 7 1
주장 1 3
파가 27 1
파가 9 1
파가 1 1
자강 1 1
파와 1 2
의견 34 1
의견 26 2
의견 15 1
의견 9 1
의견 5 1
의견 1 3
차 32 2
차 15 4
차 7 1
차 5 1
차 2 2
차 1 2
행동 1 1
때문 34 1
때문 30 1
때문 27 3
때문 20 2
때문 15 1
때문 14 1
때문 13 5
때문 10 2
때문 7 3
때문 6 1
때문 1 1
반당 9 1
반당 1 2
의총 1 1
합의점 1 1
준비 34 1
준비 32 1
준비 18 1
준비 17 1
준비 14 1
준비 1 1
모임 1 1
변화 32 1
변화 27 1
변화 25 2
변화 20 1
변화 9 2
변화 1 2
약칭 1 1
본격 1 1
수순 1 1
계기 16 1
계기 12 1
계기 5 1
계기 1 1
기정사실 7 1
기정사실 1 1
하자 21 1
하자 5 2
하자 1 1
당내 25 1
당내 1 4
내연 21 1
내연 1 1
간 34 1
간 31 1
간 28 1
간 24 1
간 21 1
간 20 3
간 15 2
간 13 2
간 12 1
간 10 2
간 8 1
간 6 1
간 5 2
간 1 1
수면 1 1
위 26 4
위 21 1
위 11 1
위 9 3
위 7 2
위 5 1
위 3 1
위 1 2
터 31 1
터 29 1
터 23 1
터 21 1
터 13 1
터 9 1
터 1 1
뿐 26 1
뿐 17 1
뿐 1 1
외부 9 2
외부 7 1
외부 1 2
추가 33 1
추가 30 1
추가 26 1
추가 25 1
추가 17 1

정부 30 4
정부 29 2
정부 28 3
정부 27 1
정부 26 6
정부 25 1
정부 22 4
정부 15 2
정부 14 1
정부 13 7
정부 12 2
정부 10 5
정부 7 1
정부 5 2
정부 4 4
정부 3 3
민간 13 2
민간 3 1
기업 34 1
기업 25 1
기업 20 8
기업 14 3
기업 12 10
기업 10 4
기업 8 1
기업 3 4
합심 3 1
경제 33 2
경제 32 1
경제 30 1
경제 29 2
경제 26 5
경제 25 2
경제 24 3
경제 22 1
경제 21 3
경제 20 5
경제 15 1
경제 14 8
경제 13 2
경제 12 3
경제 11 7
경제 10 7
경제 6 1
경제 5 4
경제 3 2
보복 26 6
보복 22 2
보복 14 2
보복 10 1
보복 8 1
보복 5 1
보복 3 2
여론 27 3
여론 26 1
여론 3 2
전달 7 1
전달 3 1
긴장감 3 1
국익 3 1
우선 10 1
우선 3 1
신중 3 1
소통 9 1
소통 5 1
소통 3 1
단기적 3 1
장기적 12 1
장기적 3 1
대책 30 1
대책 14 1
대책 12 3
대책 8 1
대책 4 3
대책 3 1
논의 7 1
논의 5 2
논의 3 1
각자 3 2
자리 25 3
자리 15 1
자리 12 1
자리 9 1
자리 6 2
자리 5 6
자리 3 1
방법 20 1
방법 6 1
방법 3 1
당적 3 2
협력 32 1
협력 22 1
협력 3 2
키 28 1
키 24 1
키 8 1
키 5 1
키 3 1
국내 33 1
국내 31 1
국내 24 2
국내 16 2
국내 12 1
국내 10 2
국내 8 1
국내 3 1
신문 27 2
신문 16 3
신문 10 2
신문 3 2
원래 3 1
자극적 3 1
4 30 1
4 28 4
4 27 1
4 23 1
4 20 1
4 17 1
4 16 1
4 15 2
4 11 1
4 8 1
4 7 1
4 3 1
투자 32 1
투자 20 1
투자 3 3
40 18 1
40 13 1
40 3 1
요즘 33 1
요즘 21 1
요즘 3 1
기사

마중물 6 1
야당 27 2
야당 26 2
야당 8 1
야당 6 4
전향 6 1
연속 6 1
본회의 25 2
본회의 8 7
본회의 6 6
선례 6 1
일인 6 1
패스트 6 2
트랙 6 2
신속 6 1
안건 8 2
안건 6 1
충돌 6 1
국면 6 1
고소 6 2
이후 24 2
이후 17 2
이후 15 2
이후 11 1
이후 8 2
이후 6 1
본격화 10 1
본격화 9 1
본격화 6 1
조사 27 2
조사 20 1
조사 19 4
조사 18 2
조사 17 1
조사 14 1
조사 10 2
조사 6 1
불응 6 2
당초 13 1
당초 9 1
당초 7 1
당초 6 2
선진 6 1
화법 6 1
위반 29 1
위반 27 1
위반 20 4
위반 17 1
위반 6 1
처벌 16 1
처벌 6 1
간과 6 1
탄압 6 1
운운 6 1
소환 6 1
납득 22 1
납득 6 1
경원 6 3
중진 9 2
중진 6 1
연석회의 6 1
지키기 6 1
공격 27 2
공격 6 1
여당 27 4
여당 8 1
여당 6 3
계속 27 1
계속 11 2
계속 7 1
계속 6 2
민의 6 1
몽니 6 1
채 6 1
막 6 1
위기 29 1
위기 21 1
위기 8 2
위기 7 1
위기 6 1
포기 22 1
포기 6 2
고발 6 1
무늬 6 1
견학 6 1
출석 6 1
놀이 6 1
전날 29 1
전날 19 1
전날 10 1
전날 6 1
청문 6 1
경과 19 1
경과 6 1
보고서 7 1
보고서 6 1
채택 6 1
윤 33 1
윤 15 24
윤 12 1
윤 6 1
검찰 20 6
검찰 17 3
검찰 15 10
검찰 6 3
총장 15 12
총장 6 2
임명 25 1
임명 15 2
임명 6 1
재가 15 1
재가 6 1
고리 6 1
공세 29 1
공세 6 2
강화 34 2
강화 33 1
강화 32 1
강화 31 2
강화 28 1
강화 25 1
강화 10 1
강화 6 1
황 20 1
황 7 6
황 6 2
교 7 4
교 6 1
정치적 15 1
정치적 8 1
정치적 7 1
정치적 6 3
중립 6 2
적격자 6 1

일반 13 11
수익 13 2
손실 33 1
손실 13 3
감내 13 1
이달 28 1
이달 22 1
이달 15 1
이달 14 1
이달 13 2
가상 13 7
시행 34 1
시행 13 2
진퇴양난 13 1
시공사 13 4
택지 13 1
실시 15 1
실시 13 1
촉각 13 1
강남 13 1
집값 13 1
지속적 13 1
우 25 2
우 16 1
우 13 1
상향 13 1
제하 13 1
마식 13 1
수준 33 2
수준 30 1
수준 24 1
수준 13 2
책정 13 2
강동구 13 1
비교 21 1
비교 13 1
가나 13 1
시세 13 2
평균 33 1
평균 13 1
가인 13 1
2569 13 1
적용 31 3
적용 13 3
올림픽 28 1
올림픽 13 1
선수촌 13 1
3700 13 1
가로 13 1
1200 13 2
면적 13 2
규모 15 1
규모 14 6
규모 13 1
대비 28 1
대비 13 2
4545 13 1
억 28 2
억 20 4
억 14 6
억 13 3
개별 13 2
최상 13 1
시나리오 13 1
3400 13 1
비용 34 1
비용 21 1
비용 13 2
셈 34 1
셈 29 1
셈 27 1
셈 26 1
셈 13 1
4000 13 2
2748 13 1
만원 16 1
만원 13 1
부가세 13 1
200 24 1
200 21 1
200 13 1
2460 13 1
6200 13 1
땅값 13 1
건축비 13 1
원가 20 2
원가 13 1
산정 13 1
액 13 1
금융 20 2
금융 13 1
사업장 14 1
사업장 13 1
2010 13 1
현대 13 2
건설 21 1
건설 13 2
건설사 13 2
이례적 13 1
지분 20 4
지분 13 8
시공 13 2
변동 13 2
이견 13 1
발생 14 2
발생 13 2
소유 13 1
비율 25 1
비율 20 1
비율 13 1
무상 13 1
보장 13 1
개발 21 1
개발 13 1
하락 13 1
미분양 13 1
위험 13 1
입찰 13 1
제로 25 1
제로 13 2
본계약 13 1
체결 

...

신고 19 1
신고 17 1
신고 16 2
신고 2 9
확인 10 1
확인 2 5
홍 33 1
홍 28 1
홍 22 1
홍 12 1
홍 2 1
기원 27 1
기원 2 1
참모 15 1
참모 5 6
참모 2 3
본부 2 3
아침 2 1
충남 2 3
진 4 1
진 2 4
서해안 2 3
고속도로 2 3
행담 2 6
휴게소 2 8
인근 19 2
인근 13 1
인근 11 3
인근 2 5
해상 23 3
해상 2 4
잠수함 2 6
고가 2 1
접수 2 3
정밀 2 1
사진 32 1
사진 31 1
사진 30 1
사진 28 1
사진 23 1
사진 19 1
사진 15 1
사진 14 1
사진 12 1
사진 9 1
사진 5 2
사진 2 1
해군 2 5
해경 2 4
함정 2 3
수색 20 3
수색 2 3
모습 34 1
모습 31 1
모습 28 2
모습 27 1
모습 26 2
모습 19 1
모습 16 1
모습 12 2
모습 9 1
모습 2 1
함대 2 2
근해 2 1
군경 2 1
소동 2 1
시민 27 1
시민 22 2
시민 2 2
분위기 29 1
분위기 28 1
분위기 4 1
분위기 2 1
속 33 2
속 23 1
속 21 1
속 16 1
속 3 2
속 2 1
의아심 2 1
표시 2 2
경찰 19 6
경찰 17 3
경찰 16 7
경찰 6 3
경찰 2 1
휴게 2 1
소 28 1
소 26 1
소 17 1
소 16 1
소 15 5
소 12 1
소 8 1
소 5 1
소 2 1
뒤편 2 1
도로 23 2
도로 9 2
도로 2 1
공사 13 1
공사 2 1
상황 34 1
상황 29 1
상황 24 1
상황 22 2
상황 20 2
상황 16 2
상황 14 1
상황 13 2
상황 12 1
상황 11 1
상황 10 1
상황 7 1
상황 5 2
상황 2 2
점검 14 1
점검 12 1
점검 2 1
분주 14 1
분주 2 1
직원 32 2
직원 2 2
업무 21 1
업무 16 2
업무 2 1
몰두 2 1
휴식 2 1
관광객 28 8
관광객 23 1
관광객 2 3
표정 2 1
식사 19 1
식사 2 1


실제 10 2
실제 4 1
영향 33 1
영향 28 2
영향 25 1
영향 23 4
영향 16 1
영향 15 1
영향 14 1
영향 10 1
영향 4 1
처우 30 1
처우 4 1
개선 30 1
개선 4 1
방안 34 1
방안 30 2
방안 26 3
방안 4 2
사납금 34 1
사납금 4 1
도입 30 1
도입 25 2
도입 4 1
이상수 4 1
씨도 4 1
기여금 34 4
기여금 30 1
기여금 4 1
오리무중 4 1
월급제 34 1
월급제 30 2
월급제 4 1
번 34 1
번 20 1
번 15 1
번 9 1
번 7 2
번 6 1
번 4 1
시행착오 4 1
재구 4 1
국토 34 6
국토 30 4
국토 4 1
교통부 34 1
교통부 30 2
교통부 4 1
성장 21 1
성장 12 2
성장 4 1
발전 34 2
발전 9 1
발전 6 1
발전 4 1
개편 34 2
개편 32 1
개편 4 1
도심 4 1
차량 34 3
차량 17 1
차량 4 1
재인 15 3
재인 7 1
재인 6 1
재인 5 3
최근 33 2
최근 30 1
최근 14 1
최근 13 1
최근 10 3
최근 5 3
차례 20 1
차례 17 1
차례 5 2
참모진 5 4
번개 5 2
오찬 5 7
을 33 2
을 29 3
을 24 1
을 16 1
을 5 1
여민 5 2
관 33 1
관 30 1
관 15 1
관 12 2
관 8 1
관 6 1
관 5 2
머리 34 1
머리 26 1
머리 12 1
머리 5 2
기자단 5 2
당일 5 1
예고 29 2
예고 5 1
부속실 5 1
상조 5 1
실장 5 1
강기 5 2
정무 5 5
산하 5 1
산업 34 1
산업 10 3
산업 5 1
통상 15 2
통상 10 1
통상 5 1
비서관 5 1
시간 34 1
시간 31 1
시간 29 5
시간 25 2
시간 13 1
시간 12 1
시간 8 1
시간 7 1
시간 6 1
시간 5 1
진행 34 1
진행 11 1
진행 5 1
경우 34 2
경우 30 3
경우 25 1
경우 14 3
경우 13 1
경우 12 1
경우 10 3
경

움직임 10 1
움직임 9 1
배신 9 2
다수 9 1
원활 14 1
원활 9 1
비대 9 2
전환 9 4
별도 9 1
이하 9 1
재선 9 1
기득권 9 2
세력 27 6
세력 9 2
태동 9 1
헌신 9 1
결의 9 1
다짐 25 1
다짐 9 1
동참 14 1
동참 9 1
양당 9 1
극복 9 1
건강 24 1
건강 9 2
당론 9 1
어제 9 2
두고 26 1
두고 9 1
격론 9 1
시기 15 1
시기 9 1
몸부림 9 1
결합 30 1
결합 9 1
학 9 2
관심 30 1
관심 15 2
관심 9 1
흥미 9 1
합 9 1
그림 21 1
그림 15 1
그림 9 1
첫발 9 1
일각 15 1
일각 9 1
전면 9 1
수록 22 1
수록 9 1
튼튼 9 1
필요 34 1
필요 30 1
필요 26 1
필요 25 1
필요 12 2
필요 9 1
로드 9 1
가급적 9 1
단계 9 4
매듭 9 1
정기 27 1
정기 9 1
연말 9 1
연초 9 1
임박 9 1
개인적 21 1
개인적 16 1
개인적 9 1
모처 9 1
얘기 33 1
얘기 13 2
얘기 9 1
가지 24 1
가지 12 1
가지 9 1
그분 9 2
최종적 9 1
허영 9 1
철새 9 1
쑥대밭 9 1
메뚜기 9 1
떼 9 1
미아 9 1
가출 9 1
구태 9 1
우두머리 9 1
패거리 9 1
도의 9 1
소재 14 13
소재 12 1
소재 10 4
부품 14 2
부품 10 1
수입 30 1
수입 14 8
수입 10 5
다변화 10 2
시동 10 1
러 10 1
복수 10 2
제의 10 1
삼성 31 1
삼성 20 23
삼성 15 1
삼성 10 1
공급 34 1
공급 30 1
공급 14 1
공급 13 1
공급 10 8
처 33 1
처 23 1
처 16 1
처 10 4
확보 34 1
확보 33 2
확보 27 2
확보 20 2
확보 14 5
확보 10 6
시장 33 2
시장 32 7
시장 28 2
시장 24 7
시장 21 1
시장 20 2
시장 10 2
일본산 14 1
일본산 10 5
시험 10 5
고순도

종합 30 3
종합 15 1
정보 30 2
정보 15 1
대림동 16 5
여경 16 6
튜브 31 1
튜브 16 1
캡 23 1
캡 16 1
동영상 31 1
동영상 27 1
동영상 16 3
남자 19 1
남자 16 1
경찰관 16 9
뺨 16 3
제압 16 6
조선족 16 3
심 21 1
심 18 1
심 17 1
심 16 1
집행 25 7
집행 20 1
집행 16 8
유예 16 4
선고 16 4
법원 20 1
법원 16 1
남부 23 2
남부 16 1
지법 17 1
지법 16 1
단 33 1
단 16 1
독 16 1
박찬 16 1
판사 17 1
판사 16 1
공무 16 4
방해 16 6
혐의 21 1
혐의 19 2
혐의 17 6
혐의 16 6
허 16 5
53 17 1
53 16 1
징역 16 2
강모 16 1
41 16 1
재판부 17 1
재판부 16 1
피고인 17 1
피고인 16 3
인정 22 1
인정 21 1
인정 16 1
반성 16 1
전력 16 1
판결 28 1
판결 16 1
체류 16 1
양형 16 1
13 16 1
쯤 18 1
쯤 17 1
쯤 16 1
구로 16 2
구의 16 1
업주 16 1
술값 16 1
시비 16 1
출동 19 1
출동 17 1
출동 16 2
강 25 1
강 17 1
강 16 2
커뮤니티 16 1
네티즌 16 1
편집 16 1
여자 19 5
여자 16 1
효용 16 1
비화 16 1
파문 16 1
침착 16 2
범인 16 1
오해 16 1
소지 20 1
소지 16 1
장면 16 1
기한 16 1
민사 16 2
소송 16 5
경찰서 19 1
경찰서 17 1
경찰서 16 1
신구 16 1
지구대 16 1
경위 19 1
경위 16 2
경장 16 1
피의 16 1
자인 16 1
112 16 3
224 16 1
손해 16 1
배상 28 1
배상 16 1
청구 16 1
피의자 16 3
폭행 17 2
폭행 16 1
욕설 16 1
신체적 16 1
정신적 16 1
불필요 16 1
공무원 16 1
사기 16 1
저하 16 1
사유 16 1
금

해 28 1
관광 28 5
61 28 1
900 28 1
09 28 2
700 28 1
38 28 1
집계 28 2
월별 28 1
전체적 28 1
77 28 1
월보 28 1
113 28 1
58 28 1
감소 28 3
과 28 1
월평균 28 1
외면 28 1
현상 28 1
소폭 28 1
중순 29 1
중순 28 1
간사이 28 1
기저 28 1
효과 28 1
추세 30 1
추세 28 1
상호 28 1
국적 28 1
453 28 1
500 28 1
대만인 28 1
콩 28 1
인은 28 1
248 28 1
110 28 1
천만 28 2
유치 28 1
오도 28 1
메 28 1
혼 28 1
타워 28 1
건물 28 1
벽면 28 1
시계 28 1
오토 28 1
행인 28 1
작품 28 1
애니메이션 28 1
거장 28 1
야자 28 1
하야 28 1
감독 30 2
감독 28 1
한미 29 1
훈련 29 7
속도 29 3
조절 29 3
응수 29 2
직접 29 2
협상 29 15
재개 29 3
기싸움 29 2
가운 29 1
데이 29 1
백악관 29 4
각료 29 2
주재 29 1
양옆 29 1
폼페이 29 2
스펜서 29 1
핵 29 5
본질적 29 1
북한 29 8
군사 29 2
대북 29 3
모건 29 1
테 29 1
국무부 29 3
판문점 29 2
진전 29 2
과의 29 1
일종 29 2
외무성 29 1
담화 29 1
확약 29 1
고유 29 1
동국대 29 1
192 29 1
동맹 29 2
연습 29 1
대규모 34 1
대규모 29 1
시뮬레이션 29 1
이마 29 1
청구서 29 2
스티븐 29 1
접근 29 1
동결 29 1
입구 29 1
아이디어 29 1
테이블 29 1
오기 29 1
직거래 29 1
촉진 29 1
지렛대 29 1
소식통 29 1
자연 29 1
난관 29 1
봉착 29 1
에스 29 1
지명자 29 1
방위비 29 3
하반기 31 1
하반기 29 1
주한 29 1
미군 29 1
증액 29 1
용석 29 1
박동 29 1
부제 30

In [95]:
V = list()
D = list()
Dictionary = defaultdict(lambda:-1)
Postings = open('Postings.dat', 'wb')

for d in collection:
    i = len(D)
    D.append(i)
    localPostings = defaultdict(int) # 빈도 저장해야되니 냅두자
    
    for t in [_[0] for _ in kkma.pos(d) if _[1].startswith("N")]:
        if t not in V:
            V.append(t)
        j = V.index(t)
        localPostings[j] += 1
        
    for j, f in localPostings.items():
        nextPosition = Dictionary[j]
        _struct = (i, f, nextPosition)
        Dictionary[j] = Postings.tell()
        Postings.write(pack("3i", i, f, nextPosition))
        
Postings.close()

In [96]:
%%timeit
with open("Postings.dat", 'rb') as Postings:
    for j in range(len(V)):
        nextPosition = Dictionary[j]
        while True:
            Postings.seek(nextPosition)
            _struct = unpack('3i', Postings.read(12))
            nextPosition = _struct[2]
            print(V[j], D[_struct[0]], _struct[1])
            if nextPosition == -1:
                break
                
# 3.43 s ± 316 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)

합리적 31 1
합리적 0 2
보수 7 1
보수 1 1
보수 0 5
주춧돌 0 2
추모 0 2
정 33 1
정 31 1
정 26 1
정 22 1
정 17 1
정 12 1
정 9 4
정 8 1
정 6 3
정 5 2
정 3 3
정 1 8
정 0 18
빈소 0 13
조문객 0 2
서울 34 1
서울 32 1
서울 30 3
서울 20 1
서울 19 3
서울 18 1
서울 16 6
서울 15 6
서울 14 6
서울 11 8
서울 10 6
서울 9 2
서울 8 5
서울 6 4
서울 4 6
서울 3 2
서울 1 3
서울 0 14
연합 30 1
연합 29 6
연합 28 4
연합 27 1
연합 26 1
연합 25 3
연합 23 5
연합 18 1
연합 15 1
연합 6 7
연합 4 4
연합 2 5
연합 1 6
연합 0 9
뉴스 33 1
뉴스 32 1
뉴스 30 2
뉴스 29 2
뉴스 28 4
뉴스 27 2
뉴스 26 2
뉴스 25 2
뉴스 23 5
뉴스 22 3
뉴스 21 2
뉴스 20 1
뉴스 18 1
뉴스 17 1
뉴스 16 1
뉴스 15 2
뉴스 14 1
뉴스 13 1
뉴스 11 1
뉴스 10 1
뉴스 7 2
뉴스 6 7
뉴스 4 4
뉴스 3 2
뉴스 2 5
뉴스 1 5
뉴스 0 9
신 15 1
신 1 1
신 0 6
기자 34 4
기자 33 1
기자 32 1
기자 31 2
기자 30 1
기자 29 1
기자 26 1
기자 25 1
기자 24 2
기자 23 2
기자 22 2
기자 21 2
기자 20 1
기자 19 1
기자 18 1
기자 17 1
기자 16 1
기자 15 1
기자 14 1
기자 13 1
기자 12 1
기자 11 1
기자 10 2
기자 9 4
기자 8 4
기자 7 2
기자 6 5
기자 4 2
기자 3 4
기자 2 3
기자 1 4
기자 0 8
17 32 1
17 30 1
17 28 1
17 27 2
17 26 4
17 23 4
17 20 1
17 19 1
17 18 2
17 17 1
17 16 1
17 15 1
17 14 2
17 13 2
17 12 2
17 11 

주장 20 6
주장 17 2
주장 11 1
주장 9 3
주장 7 1
주장 1 3
파가 27 1
파가 9 1
파가 1 1
자강 1 1
파와 1 2
의견 34 1
의견 26 2
의견 15 1
의견 9 1
의견 5 1
의견 1 3
차 32 2
차 15 4
차 7 1
차 5 1
차 2 2
차 1 2
행동 1 1
때문 34 1
때문 30 1
때문 27 3
때문 20 2
때문 15 1
때문 14 1
때문 13 5
때문 10 2
때문 7 3
때문 6 1
때문 1 1
반당 9 1
반당 1 2
의총 1 1
합의점 1 1
준비 34 1
준비 32 1
준비 18 1
준비 17 1
준비 14 1
준비 1 1
모임 1 1
변화 32 1
변화 27 1
변화 25 2
변화 20 1
변화 9 2
변화 1 2
약칭 1 1
본격 1 1
수순 1 1
계기 16 1
계기 12 1
계기 5 1
계기 1 1
기정사실 7 1
기정사실 1 1
하자 21 1
하자 5 2
하자 1 1
당내 25 1
당내 1 4
내연 21 1
내연 1 1
간 34 1
간 31 1
간 28 1
간 24 1
간 21 1
간 20 3
간 15 2
간 13 2
간 12 1
간 10 2
간 8 1
간 6 1
간 5 2
간 1 1
수면 1 1
위 26 4
위 21 1
위 11 1
위 9 3
위 7 2
위 5 1
위 3 1
위 1 2
터 31 1
터 29 1
터 23 1
터 21 1
터 13 1
터 9 1
터 1 1
뿐 26 1
뿐 17 1
뿐 1 1
외부 9 2
외부 7 1
외부 1 2
추가 33 1
추가 30 1
추가 26 1
추가 25 1
추가 17 1
추가 15 2
추가 13 3
추가 6 1
추가 5 1
추가 1 1
합류 15 1
합류 1 3
구상 1 2
중이 19 1
중이 18 1
중이 11 1
중이 1 2
결성 1 1
참여자 1 1
종회 9 1
종회 1 1
박지원 9 1
박지원 8 1
박지원 1 1
윤영 9 1
윤영 1 1
이용 22 1
이용 19 1
이용 9 1
이용 4 1
이용 1 2
주 29 1
주 21 1
주 20 1

대책 14 1
대책 12 3
대책 8 1
대책 4 3
대책 3 1
논의 7 1
논의 5 2
논의 3 1
각자 3 2
자리 25 3
자리 15 1
자리 12 1
자리 9 1
자리 6 2
자리 5 6
자리 3 1
방법 20 1
방법 6 1
방법 3 1
당적 3 2
협력 32 1
협력 22 1
협력 3 2
키 28 1
키 24 1
키 8 1
키 5 1
키 3 1
국내 33 1
국내 31 1
국내 24 2
국내 16 2
국내 12 1
국내 10 2
국내 8 1
국내 3 1
신문 27 2
신문 16 3
신문 10 2
신문 3 2
원래 3 1
자극적 3 1
4 30 1
4 28 4
4 27 1
4 23 1
4 20 1
4 17 1
4 16 1
4 15 2
4 11 1
4 8 1
4 7 1
4 3 1
투자 32 1
투자 20 1
투자 3 3
40 18 1
40 13 1
40 3 1
요즘 33 1
요즘 21 1
요즘 3 1
기사 34 9
기사 30 2
기사 26 19
기사 4 7
기사 3 8
낯짝 3 1
하나 34 1
하나 27 1
하나 25 2
하나 24 1
하나 12 1
하나 7 1
하나 3 1
로 33 1
로 32 4
로 25 4
로 24 1
로 21 1
로 5 2
로 3 1
15 23 1
15 17 1
15 13 1
15 5 1
15 3 3
국채 3 1
보상 3 1
동학 3 1
운동 21 2
운동 7 2
운동 3 1
세기 3 1
해결책 26 1
해결책 3 1
제시 26 3
제시 20 1
제시 3 1
반일 26 1
반일 3 1
불 21 1
불 15 1
불 7 1
불 3 1
7 33 1
7 29 1
7 27 2
7 25 1
7 20 1
7 10 1
7 3 1
라 29 1
라 27 1
라 25 1
라 24 2
라 21 1
라 11 1
라 3 1
일본판 26 5
일본판 3 2
한국인 28 7
한국인 26 2
한국인 3 2
편협 3 1
현재 34 1
현재 31 1
현재 30 2
현재 24 1
현재 23 1
현재 21 1
현재 15 1
현재 14 4
현재 12 1
현재 10 2

되풀이 22 1
되풀이 6 1
법안 34 1
법안 8 11
법안 6 3
심사 6 3
회기 6 1
이틀 30 1
이틀 8 3
이틀 6 3
6 28 5
6 16 1
6 15 1
6 14 1
6 6 2
임시 6 2
빈손 6 1
종료 20 1
종료 6 2
제기 31 1
제기 27 1
제기 16 3
제기 7 1
제기 6 1
하루 30 1
하루 25 1
하루 21 1
하루 6 2
정국 6 1
돌파구 6 1
이목 6 1
이인 6 1
하사 6 1
이인영 6 2
정쟁 6 1
방탄 6 3
수단 6 1
민생 8 6
민생 6 1
마중물 6 1
야당 27 2
야당 26 2
야당 8 1
야당 6 4
전향 6 1
연속 6 1
본회의 25 2
본회의 8 7
본회의 6 6
선례 6 1
일인 6 1
패스트 6 2
트랙 6 2
신속 6 1
안건 8 2
안건 6 1
충돌 6 1
국면 6 1
고소 6 2
이후 24 2
이후 17 2
이후 15 2
이후 11 1
이후 8 2
이후 6 1
본격화 10 1
본격화 9 1
본격화 6 1
조사 27 2
조사 20 1
조사 19 4
조사 18 2
조사 17 1
조사 14 1
조사 10 2
조사 6 1
불응 6 2
당초 13 1
당초 9 1
당초 7 1
당초 6 2
선진 6 1
화법 6 1
위반 29 1
위반 27 1
위반 20 4
위반 17 1
위반 6 1
처벌 16 1
처벌 6 1
간과 6 1
탄압 6 1
운운 6 1
소환 6 1
납득 22 1
납득 6 1
경원 6 3
중진 9 2
중진 6 1
연석회의 6 1
지키기 6 1
공격 27 2
공격 6 1
여당 27 4
여당 8 1
여당 6 3
계속 27 1
계속 11 2
계속 7 1
계속 6 2
민의 6 1
몽니 6 1
채 6 1
막 6 1
위기 29 1
위기 21 1
위기 8 2
위기 7 1
위기 6 1
포기 22 1
포기 6 2
고발 6 1
무늬 6 1
견학 6 1
출석 6 1
놀이 6 1
전날 29 1
전날 19 1
전날 10 1
전날 6 1
청문 6 1
경과 19 1
경과 6 1
보고서 7 1
보고서 6

셈 27 1
셈 26 1
셈 13 1
4000 13 2
2748 13 1
만원 16 1
만원 13 1
부가세 13 1
200 24 1
200 21 1
200 13 1
2460 13 1
6200 13 1
땅값 13 1
건축비 13 1
원가 20 2
원가 13 1
산정 13 1
액 13 1
금융 20 2
금융 13 1
사업장 14 1
사업장 13 1
2010 13 1
현대 13 2
건설 21 1
건설 13 2
건설사 13 2
이례적 13 1
지분 20 4
지분 13 8
시공 13 2
변동 13 2
이견 13 1
발생 14 2
발생 13 2
소유 13 1
비율 25 1
비율 20 1
비율 13 1
무상 13 1
보장 13 1
개발 21 1
개발 13 1
하락 13 1
미분양 13 1
위험 13 1
입찰 13 1
제로 25 1
제로 13 2
본계약 13 1
체결 13 1
설계 28 1
설계 21 1
설계 13 1
변경 20 6
변경 13 1
최초 25 1
최초 24 2
최초 13 1
의미 33 1
의미 29 1
의미 27 1
의미 26 1
의미 13 1
집행부 13 1
귀속 13 1
가가 13 2
누 13 1
질 29 1
질 21 1
질 13 2
지에 34 1
지에 13 1
무작정 13 1
제야 13 1
말로 13 1
서민 13 3
5779 13 1
30 33 1
30 28 1
30 23 2
30 22 1
30 21 1
30 19 1
30 15 3
30 13 1
중반 13 1
가장 13 1
아이 31 1
아이 25 1
아이 13 1
청약 21 1
청약 13 3
모든 26 1
모든 13 1
대출 13 1
노모 13 1
노후 13 1
자금 13 1
재개발 13 2
입주권 13 1
거액 13 1
지불 13 1
땅 13 1
피 24 1
피 17 1
피 13 1
살 13 1
이것 26 1
이것 13 1
로또 13 1
주라 13 1
경쟁 24 1
경쟁 13 1
집 21 1
집 13 1
현금 13 1
부자 29 1
부자 13 1
잔치 13 1
범주 13 1
보세 33 1
보세 2

...

차 7 1
차 5 1
차 2 2
차 1 2
행동 1 1
때문 34 1
때문 30 1
때문 27 3
때문 20 2
때문 15 1
때문 14 1
때문 13 5
때문 10 2
때문 7 3
때문 6 1
때문 1 1
반당 9 1
반당 1 2
의총 1 1
합의점 1 1
준비 34 1
준비 32 1
준비 18 1
준비 17 1
준비 14 1
준비 1 1
모임 1 1
변화 32 1
변화 27 1
변화 25 2
변화 20 1
변화 9 2
변화 1 2
약칭 1 1
본격 1 1
수순 1 1
계기 16 1
계기 12 1
계기 5 1
계기 1 1
기정사실 7 1
기정사실 1 1
하자 21 1
하자 5 2
하자 1 1
당내 25 1
당내 1 4
내연 21 1
내연 1 1
간 34 1
간 31 1
간 28 1
간 24 1
간 21 1
간 20 3
간 15 2
간 13 2
간 12 1
간 10 2
간 8 1
간 6 1
간 5 2
간 1 1
수면 1 1
위 26 4
위 21 1
위 11 1
위 9 3
위 7 2
위 5 1
위 3 1
위 1 2
터 31 1
터 29 1
터 23 1
터 21 1
터 13 1
터 9 1
터 1 1
뿐 26 1
뿐 17 1
뿐 1 1
외부 9 2
외부 7 1
외부 1 2
추가 33 1
추가 30 1
추가 26 1
추가 25 1
추가 17 1
추가 15 2
추가 13 3
추가 6 1
추가 5 1
추가 1 1
합류 15 1
합류 1 3
구상 1 2
중이 19 1
중이 18 1
중이 11 1
중이 1 2
결성 1 1
참여자 1 1
종회 9 1
종회 1 1
박지원 9 1
박지원 8 1
박지원 1 1
윤영 9 1
윤영 1 1
이용 22 1
이용 19 1
이용 9 1
이용 4 1
이용 1 2
주 29 1
주 21 1
주 20 1
주 11 1
주 9 1
주 1 3
장병 9 1
장병 1 1
정숙 9 1
정숙 1 1
정인 9 1
정인 1 1
천 28 8
천 9 1
천 1 1
정배 9 1
정배 1 1
경환 9 1
경환 1 1
이상 33 1
이상 30 1
이상 27 1
이상 15 2

7 27 2
7 25 1
7 20 1
7 10 1
7 3 1
라 29 1
라 27 1
라 25 1
라 24 2
라 21 1
라 11 1
라 3 1
일본판 26 5
일본판 3 2
한국인 28 7
한국인 26 2
한국인 3 2
편협 3 1
현재 34 1
현재 31 1
현재 30 2
현재 24 1
현재 23 1
현재 21 1
현재 15 1
현재 14 4
현재 12 1
현재 10 2
현재 3 1
야 26 3
야 12 2
야 3 1
재 26 3
재 11 1
재 5 3
재 3 1
팬 26 3
팬 3 1
국제 26 3
국제 25 1
국제 21 1
국제 20 2
국제 12 1
국제 3 1
면 27 1
면 26 1
면 16 2
면 15 1
면 3 1
칼럼 26 6
칼럼 3 2
외교 29 2
외교 26 3
외교 25 2
외교 3 2
다음 3 1
날 27 1
날 12 2
날 3 1
랭크 3 1
일본인 26 3
일본인 3 1
번역 26 1
번역 3 1
이해 26 1
이해 21 1
이해 6 1
이해 5 1
이해 3 1
진정 22 1
진정 3 1
목 27 1
목 17 1
목 3 1
소리 33 3
소리 7 1
소리 3 1
반영 29 1
반영 26 1
반영 7 1
반영 3 2
조국 26 1
조국 5 1
조국 3 2
민정 26 1
민정 15 1
민정 5 3
민정 3 3
방송 32 1
방송 3 1
화면 31 2
화면 3 1
캡처 16 1
캡처 3 1
표현 33 2
표현 26 2
표현 3 2
항의 26 1
항의 8 1
항의 3 1
책임감 3 1
답변 15 1
답변 3 1
특정 3 2
언론사 3 1
실명 3 1
건 33 4
건 29 1
건 26 2
건 21 1
건 20 1
건 9 1
건 8 1
건 6 1
건 3 1
시각 3 1
평가 31 1
평가 20 3
평가 16 2
평가 15 1
평가 5 1
평가 4 2
평가 3 1
선 33 1
선 30 2
선 27 1
선 26 1
선 21 1
선 20 1
선 15 1
선 12 2
선 9 2
선 7 1
선 6 1
선 5 1
선 4 1
선 3 2
정면 26 1

전망 13 1
전망 10 1
전망 7 1
광주 7 3
민주화 21 3
민주화 7 2
공청회 7 2
폄훼 7 2
징계 7 2
원권 7 1
직 24 1
직 20 1
직 7 4
논란 34 1
논란 20 1
논란 16 5
논란 7 1
판단 29 1
판단 24 1
판단 20 3
판단 7 2
맹우 7 1
사무총장 7 2
자청 7 1
어젯밤 7 2
사무처 7 1
당헌 7 4
당규 7 4
직도 7 1
박탈 7 2
묵살 7 1
수차례 20 1
수차례 13 1
수차례 7 1
전화 27 1
전화 17 1
전화 7 1
문건 7 2
입수 7 1
보고 33 1
보고 7 1
상 7 2
자가 28 1
자가 7 1
회복 7 2
부담 33 1
부담 13 1
부담 7 1
최종 11 1
최종 10 1
최종 7 1
결론 7 1
법률 20 2
법률 7 2
명확성 7 1
원칙 29 1
원칙 25 1
원칙 20 1
원칙 7 1
근거 27 1
근거 20 2
근거 7 2
당사자 7 1
이익 21 1
이익 13 2
이익 10 1
이익 7 1
차명 7 1
협위 7 3
장과 15 2
장과 7 1
형평 34 1
형평 7 1
거론 15 3
거론 7 1
세월 7 3
막말 7 5
위원장 25 17
위원장 8 1
위원장 7 1
원장 7 2
조직 7 1
부총장 7 1
와의 7 1
통화 26 1
통화 25 1
통화 21 1
통화 7 1
임면권 7 1
면직 7 1
보완 7 1
개 31 2
개 24 1
개 22 1
개 17 1
개 14 4
개 8 2
개 7 2
답 7 1
이종명 7 2
제명 7 3
북한군 7 1
개입 7 1
폭동 7 1
윤리 7 2
확정 13 5
확정 7 1
상정 12 1
상정 8 1
상정 7 1
회가 7 1
정상화 7 1
특위 7 1
결과 32 1
결과 31 1
결과 27 2
결과 25 1
결과 14 1
결과 13 1
결과 7 2
후폭 7 1
일단 10 1
일단 7 1
속내 7 1
명이 7 1
의결 8 1
의결 7 1
의석수 27 2
의석수 7 1
부결 7 1
포화 7 1
리더십 7 2
단추 7 1
속앓이 1

현지 25 2
현지 14 1
안정적 32 1
안정적 30 1
안정적 14 1
해본 14 1
화이트 27 1
화이트 14 1
리스트 33 1
리스트 14 1
수급 34 1
수급 14 1
오랫동안 14 1
제재 29 1
제재 14 2
결정적 14 1
중요 29 1
중요 27 1
중요 14 1
가공선 14 2
충진 14 1
바니시 14 1
불가능 14 1
올 33 1
올 29 2
올 28 5
올 24 2
올 14 1
상반기 31 2
상반기 28 4
상반기 14 1
연간 14 3
250 14 1
1400 14 1
나라 28 1
나라 26 1
나라 24 1
나라 22 1
나라 21 1
나라 14 1
재고 14 1
전기 14 2
폴리 14 1
이미드 14 1
모화 14 2
학과 29 1
학과 20 1
학과 14 2
모그룹 14 1
계열사 14 2
모전 14 1
기가 14 1
만큼 31 1
만큼 24 1
만큼 20 1
만큼 14 1
적극적 27 1
적극적 14 1
자동차 25 2
자동차 14 2
전문 20 2
전문 14 1
자회사 20 2
자회사 14 1
코리아 34 6
코리아 31 3
코리아 14 3
노심초사 14 1
퓨즈 14 2
직접적 14 1
800 18 1
800 14 1
매출 14 2
목표 32 1
목표 28 1
목표 14 2
달성 14 1
중앙지 15 4
검장 15 4
대진 15 4
유력 15 2
국정원 15 2
댓 26 4
댓 15 4
국정 15 3
농단 15 4
특검 15 6
팀 21 2
팀 15 5
요직 15 2
발탁 25 2
발탁 15 3
간부급 15 1
단행 15 3
열 15 3
차기 25 10
차기 15 13
청문회 15 3
질의 15 1
데일리 30 3
데일리 15 3
일경 15 2
밑 26 1
밑 15 2
법조계 15 3
사단 20 1
사단 15 3
행보 15 1
관전 15 1
포인트 15 1
25 30 1
25 24 2
25 15 3
59 30 1
59 15 1
연수원 15 2
취임 32 2
취임 25 2
취임 15 4
검사장 15 4
고위직 

임원 25 1
당제 25 1
보육 25 1
증대 25 1
최저 25 1
임금제 25 1
동성 25 1
결혼 25 1
은행 25 1
총재 25 3
내정 25 3
크리스 25 1
라가 25 2
사직서 25 1
제출 25 1
상임 25 1
미 29 6
미 28 1
미 25 1
벨기에 25 1
호세 25 1
보 25 1
스페인 25 1
공석 25 1
레트 25 1
카 25 1
바우어 25 1
모바일 33 1
모바일 29 1
모바일 25 1
사이트 26 8
랭킹 26 5
상위권 26 2
차지 32 2
차지 30 1
차지 28 2
차지 27 1
차지 26 3
아베 27 5
아베 26 1
신조 27 2
신조 26 1
포털 26 2
회수 26 2
단어 34 1
단어 26 2
바꾸기 26 1
연재 26 1
부정적 30 1
부정적 26 1
대조적 26 1
다음날 26 1
중재 29 1
중재 26 5
설치 28 1
설치 26 2
거부 30 1
거부 26 5
외교적 26 2
처사 26 1
묘사 26 1
양국 29 1
양국 28 1
양국 26 1
상대국 26 1
칸 26 1
관방 26 1
비중 28 2
비중 26 1
태도 26 2
경화 26 1
외교가 26 1
경색 26 1
연일 26 1
자극 26 1
감정적 26 1
실효 26 1
해법 26 1
일간 26 1
게재 26 2
명분 26 1
한국어 26 1
워싱턴 29 1
워싱턴 26 3
무관심 26 1
세계 26 1
부당성 26 1
무용지물 26 1
당국자 26 2
파견 26 1
외교전 26 1
불가 26 1
자력 26 1
고도 26 1
한쪽 26 1
편 26 1
상단 26 1
배치 26 1
작성 26 2
비방 26 1
비난 29 2
비난 26 1
국력 26 1
싸움 26 2
상대 26 1
철회 26 1
조롱 26 1
조회 26 1
유인 26 1
고조 26 1
우민화 26 1
란 26 1
세원 26 1
공명 27 3
연립 27 4
과반 27 2
획득 34 1
획득 27 2
무 27 1
개헌 27 8
의석 27 3
묘 27 1
지바현 

in-memory
1. defaultdict(defaultdict)
2. Postings

on-dist
3. character
4. byte

속도
2 > 1 > 4 > 3
의도한것
2 > 4 > 3 > 1

데이터가 많으면 많을 수록 파일을 사용하는게 빠르다.